In [1]:
'''Trains a simple deep NN on the MNIST dataset.
Gets to 98.40% test accuracy after 20 epochs
(there is *a lot* of margin for parameter tuning).
2 seconds per epoch on a K520 GPU.
'''
import keras
from keras.datasets import mnist
from keras.models import Model, Sequential
from keras.layers import Input, Dense, Dropout, Activation
from keras.optimizers import RMSprop
from keras.callbacks import CSVLogger, TensorBoard, ReduceLROnPlateau, EarlyStopping
import os
from keras.layers.noise import AlphaDropout
import keras.activations

Using TensorFlow backend.


In [2]:
batch_size = 64
num_classes = 10
epochs = 100
units = 64
experiments = 5
activations = ['sigmoid', 'tanh', 'relu', 'linear', 'elu', 'softplus', 'softsign', 'hard_sigmoid', 'LeakyReLU', 'PReLU', 'ThresholdedReLU']
# activations = ['hard_sigmoid']
optimizers = ['rmsp', 'adam', 'sgd', 'Adagrad', 'Adadelta', 'Adamax', 'Nadam']
# optimizers = ['sgd']

save_dir = os.path.join(os.getcwd(), 'saved_models')
# the data, shuffled and split between train and test sets
(x_train, y_train), (x_test, y_test) = mnist.load_data()

In [3]:
x_train = x_train.reshape(60000, 784)
x_test = x_test.reshape(10000, 784)
x_train = x_train.astype('float32')
x_test = x_test.astype('float32')
x_train /= 255
x_test /= 255
print(x_train.shape[0], 'train samples')
print(x_test.shape[0], 'test samples')

# convert class vectors to binary class matrices
y_train = keras.utils.to_categorical(y_train, num_classes)
y_test = keras.utils.to_categorical(y_test, num_classes)

60000 train samples
10000 test samples


## Train per each activation function

In [4]:
for act in activations:
    for opt in optimizers:
        print("Training for activation " + act + " with optimizer " + opt)
        
        # Selecting activation function
        if act == 'sigmoid':
            activation = Activation(keras.activations.sigmoid)
        elif act == 'tanh':
            activation = Activation(keras.activations.tanh)
        elif act == 'relu':
            activation = Activation(keras.activations.relu)
        elif act == 'linear':
            activation = Activation(keras.activations.linear)
        elif act == 'elu':
            activation = Activation(keras.activations.elu)
        elif act == 'softplus':
            activation = Activation(keras.activations.softplus)
        elif act == 'softsign':
            activation = Activation(keras.activations.softsign)
        elif act == 'hard_sigmoid':
            activation = Activation(keras.activations.hard_sigmoid)
        elif act == 'LeakyReLU':
            activation = keras.layers.advanced_activations.LeakyReLU()
        elif act == 'PReLU':
            activation = keras.layers.advanced_activations.PReLU()
        elif act == 'ThresholdedReLU':
            activation = keras.layers.advanced_activations.ThresholdedReLU(theta=0.7) # As proposed in Konda, Memisevic and Krueger (2015)
        
        # Selecting optimizer
        if opt == 'rmsp':
            optimizer = keras.optimizers.rmsprop(lr=0.001)                
        elif opt == 'adam':
            optimizer = keras.optimizers.Adam()
        elif opt == 'sgd':
            optimizer = keras.optimizers.SGD()
        elif opt == 'Adagrad':
            optimizer = keras.optimizers.Adagrad()
        elif opt == 'Adadelta':
            optimizer = keras.optimizers.Adadelta()
        elif opt == 'Adamax':
            optimizer = keras.optimizers.Adamax()
        elif opt == 'Nadam':
            optimizer = keras.optimizers.Nadam()

        for i in range(experiments):
            model_name = 'mnist_' + act + "_" + opt + '_' + str(i)
            inputs = Input(shape=(784,))
            x = Dense(units)(inputs)
            x = activation(x)
            x = Dropout(0.2)(x)
            x = Dense(units)(x)
            x = activation(x)
            x = Dropout(0.2)(x)
            predictions = Dense(num_classes, activation='softmax')(x)
            model = Model(inputs=inputs, outputs=predictions)

            

                
            model.compile(loss='categorical_crossentropy',
                              optimizer=optimizer,
                              metrics=['accuracy'])
            print('-'*30)
            print('Experiment', i)

            csv_logger = CSVLogger('./logs/%s_%d.csv' % (model_name, units), append=False, separator=';')
            #reduce_lr = ReduceLROnPlateau(monitor='val_acc', factor=0.2, patience=5, verbose=0, mode='auto', epsilon=0.0001, cooldown=2, min_lr=0)
            #early_stopping = EarlyStopping(monitor='val_acc', min_delta=0, patience=15, verbose=1, mode='auto')
#             tb = TensorBoard(log_dir='./tb_logs/' + model_name + '_' + str(units), histogram_freq=0, batch_size=32, write_graph=True, write_grads=False, write_images=False, embeddings_freq=0, embeddings_layer_names=None, embeddings_metadata=None)
            history = model.fit(x_train, y_train,
                                batch_size=batch_size,
                                epochs=epochs,
                                verbose=1,
                                validation_data=(x_test, y_test), callbacks=[csv_logger])

            if not os.path.isdir(save_dir):
                os.makedirs(save_dir)
            model_path = os.path.join(save_dir, model_name + ".h5")
#             model.save(model_path)

            score = model.evaluate(x_test, y_test, verbose=0)
            print('Test loss:', score[0])
            print('Test accuracy:', score[1])

Training for activation sigmoid with optimizer rmsp
------------------------------
Experiment 0
Train on 60000 samples, validate on 10000 samples
Epoch 1/100
60000/60000 [==============================] - 5s 77us/step - loss: 0.3680 - acc: 0.8903 - val_loss: 0.1900 - val_acc: 0.9449
Epoch 2/100
60000/60000 [==============================] - 4s 64us/step - loss: 0.2091 - acc: 0.9391 - val_loss: 0.1586 - val_acc: 0.9528
Epoch 3/100
60000/60000 [==============================] - 4s 63us/step - loss: 0.1834 - acc: 0.9477 - val_loss: 0.1283 - val_acc: 0.9615
Epoch 4/100
60000/60000 [==============================] - 4s 62us/step - loss: 0.1676 - acc: 0.9524 - val_loss: 0.1210 - val_acc: 0.9628
Epoch 5/100
60000/60000 [==============================] - 4s 68us/step - loss: 0.1578 - acc: 0.9554 - val_loss: 0.1289 - val_acc: 0.9671
Epoch 6/100
60000/60000 [==============================] - 4s 72us/step - loss: 0.1505 - acc: 0.9580 - val_loss: 0.1250 - val_acc: 0.9675
Epoch 7/100
60000/60000 [=

Epoch 59/100
60000/60000 [==============================] - 4s 68us/step - loss: 0.1555 - acc: 0.9692 - val_loss: 0.1739 - val_acc: 0.9707
Epoch 60/100
60000/60000 [==============================] - 4s 70us/step - loss: 0.1535 - acc: 0.9693 - val_loss: 0.1931 - val_acc: 0.9695
Epoch 61/100
60000/60000 [==============================] - 4s 60us/step - loss: 0.1522 - acc: 0.9692 - val_loss: 0.1874 - val_acc: 0.9699
Epoch 62/100
60000/60000 [==============================] - 3s 55us/step - loss: 0.1565 - acc: 0.9698 - val_loss: 0.1787 - val_acc: 0.9723
Epoch 63/100
60000/60000 [==============================] - 3s 55us/step - loss: 0.1548 - acc: 0.9697 - val_loss: 0.1828 - val_acc: 0.9702
Epoch 64/100
60000/60000 [==============================] - 4s 59us/step - loss: 0.1601 - acc: 0.9697 - val_loss: 0.1934 - val_acc: 0.9702
Epoch 65/100
60000/60000 [==============================] - 4s 62us/step - loss: 0.1550 - acc: 0.9699 - val_loss: 0.1839 - val_acc: 0.9712
Epoch 66/100
60000/60000 [=

Epoch 17/100
60000/60000 [==============================] - 4s 59us/step - loss: 0.1395 - acc: 0.9647 - val_loss: 0.1347 - val_acc: 0.9709
Epoch 18/100
60000/60000 [==============================] - 4s 62us/step - loss: 0.1392 - acc: 0.9646 - val_loss: 0.1435 - val_acc: 0.9693
Epoch 19/100
60000/60000 [==============================] - 3s 57us/step - loss: 0.1377 - acc: 0.9662 - val_loss: 0.1495 - val_acc: 0.9685
Epoch 20/100
60000/60000 [==============================] - 3s 58us/step - loss: 0.1366 - acc: 0.9674 - val_loss: 0.1436 - val_acc: 0.9710
Epoch 21/100
60000/60000 [==============================] - 3s 58us/step - loss: 0.1429 - acc: 0.9669 - val_loss: 0.1487 - val_acc: 0.9705
Epoch 22/100
60000/60000 [==============================] - 4s 63us/step - loss: 0.1356 - acc: 0.9664 - val_loss: 0.1528 - val_acc: 0.9685
Epoch 23/100
60000/60000 [==============================] - 4s 59us/step - loss: 0.1390 - acc: 0.9673 - val_loss: 0.1453 - val_acc: 0.9705
Epoch 24/100
60000/60000 [=

60000/60000 [==============================] - 4s 68us/step - loss: 0.1448 - acc: 0.9678 - val_loss: 0.1728 - val_acc: 0.9711
Epoch 34/100
60000/60000 [==============================] - 4s 66us/step - loss: 0.1434 - acc: 0.9686 - val_loss: 0.1657 - val_acc: 0.9710
Epoch 35/100
60000/60000 [==============================] - 4s 72us/step - loss: 0.1455 - acc: 0.9685 - val_loss: 0.1684 - val_acc: 0.9696
Epoch 36/100
60000/60000 [==============================] - 3s 55us/step - loss: 0.1423 - acc: 0.9682 - val_loss: 0.1634 - val_acc: 0.9702
Epoch 37/100
60000/60000 [==============================] - 4s 66us/step - loss: 0.1462 - acc: 0.9678 - val_loss: 0.1789 - val_acc: 0.9685
Epoch 38/100
60000/60000 [==============================] - 3s 55us/step - loss: 0.1375 - acc: 0.9697 - val_loss: 0.1702 - val_acc: 0.9698
Epoch 39/100
60000/60000 [==============================] - 3s 55us/step - loss: 0.1449 - acc: 0.9694 - val_loss: 0.1660 - val_acc: 0.9712
Epoch 40/100
60000/60000 [==============

60000/60000 [==============================] - 3s 56us/step - loss: 0.1698 - acc: 0.9694 - val_loss: 0.2398 - val_acc: 0.9668
Epoch 93/100
60000/60000 [==============================] - 4s 67us/step - loss: 0.1604 - acc: 0.9702 - val_loss: 0.2315 - val_acc: 0.9671
Epoch 94/100
60000/60000 [==============================] - 4s 66us/step - loss: 0.1664 - acc: 0.9705 - val_loss: 0.2371 - val_acc: 0.9668
Epoch 95/100
60000/60000 [==============================] - 4s 67us/step - loss: 0.1646 - acc: 0.9706 - val_loss: 0.2353 - val_acc: 0.9649
Epoch 96/100
60000/60000 [==============================] - 4s 62us/step - loss: 0.1663 - acc: 0.9709 - val_loss: 0.2263 - val_acc: 0.9665
Epoch 97/100
60000/60000 [==============================] - 4s 71us/step - loss: 0.1720 - acc: 0.9692 - val_loss: 0.2358 - val_acc: 0.9654
Epoch 98/100
60000/60000 [==============================] - 5s 76us/step - loss: 0.1740 - acc: 0.9690 - val_loss: 0.2333 - val_acc: 0.9669
Epoch 99/100
60000/60000 [==============

...

Epoch 6/100
60000/60000 [==============================] - 28s 465us/step - loss: 0.2414 - acc: 0.9252 - val_loss: 0.1492 - val_acc: 0.9580
Epoch 7/100
60000/60000 [==============================] - 29s 475us/step - loss: 0.2309 - acc: 0.9285 - val_loss: 0.1538 - val_acc: 0.9549
Epoch 8/100
60000/60000 [==============================] - 29s 484us/step - loss: 0.2250 - acc: 0.9297 - val_loss: 0.1544 - val_acc: 0.9552
Epoch 9/100
60000/60000 [==============================] - 28s 472us/step - loss: 0.2196 - acc: 0.9318 - val_loss: 0.1518 - val_acc: 0.9549
Epoch 10/100
60000/60000 [==============================] - 27s 452us/step - loss: 0.2145 - acc: 0.9335 - val_loss: 0.1555 - val_acc: 0.9556
Epoch 11/100
60000/60000 [==============================] - 26s 436us/step - loss: 0.2099 - acc: 0.9349 - val_loss: 0.1517 - val_acc: 0.9574
Epoch 12/100
60000/60000 [==============================] - 26s 429us/step - loss: 0.2050 - acc: 0.9361 - val_loss: 0.1532 - val_acc: 0.9574
Epoch 13/100
6000

60000/60000 [==============================] - 27s 453us/step - loss: 0.3494 - acc: 0.8844 - val_loss: 0.2296 - val_acc: 0.9302
Epoch 22/100
60000/60000 [==============================] - 28s 463us/step - loss: 0.3483 - acc: 0.8840 - val_loss: 0.2416 - val_acc: 0.9260
Epoch 23/100
60000/60000 [==============================] - 27s 457us/step - loss: 0.3518 - acc: 0.8831 - val_loss: 0.2404 - val_acc: 0.9303
Epoch 24/100
60000/60000 [==============================] - 27s 451us/step - loss: 0.3509 - acc: 0.8824 - val_loss: 0.2572 - val_acc: 0.9249
Epoch 25/100
60000/60000 [==============================] - 27s 457us/step - loss: 0.3485 - acc: 0.8842 - val_loss: 0.2409 - val_acc: 0.9289
Epoch 26/100
60000/60000 [==============================] - 28s 468us/step - loss: 0.3433 - acc: 0.8861 - val_loss: 0.2418 - val_acc: 0.9292
Epoch 27/100
60000/60000 [==============================] - 27s 453us/step - loss: 0.3397 - acc: 0.8863 - val_loss: 0.2413 - val_acc: 0.9243
Epoch 28/100
60000/60000 [

60000/60000 [==============================] - 27s 458us/step - loss: 0.6463 - acc: 0.7854 - val_loss: 0.4429 - val_acc: 0.8862
Epoch 37/100
60000/60000 [==============================] - 29s 479us/step - loss: 0.6360 - acc: 0.7889 - val_loss: 0.4041 - val_acc: 0.8845
Epoch 38/100
60000/60000 [==============================] - 28s 469us/step - loss: 0.6389 - acc: 0.7887 - val_loss: 0.4364 - val_acc: 0.8717
Epoch 39/100
60000/60000 [==============================] - 28s 468us/step - loss: 0.6472 - acc: 0.7846 - val_loss: 0.4250 - val_acc: 0.8939
Epoch 40/100
60000/60000 [==============================] - 28s 468us/step - loss: 0.6437 - acc: 0.7848 - val_loss: 0.4154 - val_acc: 0.8948
Epoch 41/100
60000/60000 [==============================] - 28s 472us/step - loss: 0.6401 - acc: 0.7856 - val_loss: 0.4383 - val_acc: 0.8898
Epoch 42/100
60000/60000 [==============================] - 28s 472us/step - loss: 0.6554 - acc: 0.7799 - val_loss: 0.4409 - val_acc: 0.8859
Epoch 43/100
60000/60000 [

60000/60000 [==============================] - 27s 455us/step - loss: 0.4506 - acc: 0.8503 - val_loss: 0.2909 - val_acc: 0.9244
Epoch 52/100
60000/60000 [==============================] - 28s 465us/step - loss: 0.4471 - acc: 0.8510 - val_loss: 0.3008 - val_acc: 0.9220
Epoch 53/100
60000/60000 [==============================] - 28s 470us/step - loss: 0.4542 - acc: 0.8475 - val_loss: 0.3047 - val_acc: 0.9234
Epoch 54/100
60000/60000 [==============================] - 28s 466us/step - loss: 0.4519 - acc: 0.8507 - val_loss: 0.3086 - val_acc: 0.9177
Epoch 55/100
60000/60000 [==============================] - 28s 469us/step - loss: 0.4476 - acc: 0.8508 - val_loss: 0.2921 - val_acc: 0.9226
Epoch 56/100
60000/60000 [==============================] - 29s 477us/step - loss: 0.4525 - acc: 0.8502 - val_loss: 0.3090 - val_acc: 0.9221
Epoch 57/100
60000/60000 [==============================] - 29s 475us/step - loss: 0.4520 - acc: 0.8507 - val_loss: 0.3017 - val_acc: 0.9221
Epoch 58/100
60000/60000 [

60000/60000 [==============================] - 29s 477us/step - loss: 0.5321 - acc: 0.8276 - val_loss: 0.3865 - val_acc: 0.9054
Epoch 67/100
60000/60000 [==============================] - 29s 481us/step - loss: 0.5331 - acc: 0.8283 - val_loss: 0.3782 - val_acc: 0.9082
Epoch 68/100
60000/60000 [==============================] - 27s 457us/step - loss: 0.5261 - acc: 0.8303 - val_loss: 0.3795 - val_acc: 0.9072
Epoch 69/100
60000/60000 [==============================] - 28s 465us/step - loss: 0.5322 - acc: 0.8276 - val_loss: 0.3728 - val_acc: 0.9133
Epoch 70/100
60000/60000 [==============================] - 28s 462us/step - loss: 0.5322 - acc: 0.8283 - val_loss: 0.3856 - val_acc: 0.9087
Epoch 71/100
60000/60000 [==============================] - 28s 466us/step - loss: 0.5355 - acc: 0.8282 - val_loss: 0.3851 - val_acc: 0.9100
Epoch 72/100
60000/60000 [==============================] - 28s 466us/step - loss: 0.5366 - acc: 0.8266 - val_loss: 0.3804 - val_acc: 0.9110
Epoch 73/100
60000/60000 [

# SeLU
This one has special requirements

In [ ]:
for opt in optimizers:
    print("Training for activation SeLU with optimizer " + opt)
    for i in range(experiments):
        model_name = 'mnist_selu_' + opt + '_' + str(i) 
        inputs = Input(shape=(784,))
        x = Dense(units, activation='selu', kernel_initializer='lecun_normal')(inputs)
        x = AlphaDropout(0.2)(x)
        x = Dense(units, activation='selu', kernel_initializer='lecun_normal')(x)
        x = AlphaDropout(0.2)(x)
        predictions = Dense(num_classes, activation='softmax')(x)
        model = Model(inputs=inputs, outputs=predictions)

        if opt == 'rmsp':
            optimizer = keras.optimizers.rmsprop(lr=0.001)                
        elif opt == 'adam':
            optimizer = keras.optimizers.Adam()
        elif opt == 'sgd':
            optimizer = keras.optimizers.SGD()
        elif opt == 'Adagrad':
            optimizer = keras.optimizers.Adagrad()
        elif opt == 'Adadelta':
            optimizer = keras.optimizers.Adadelta()
        elif opt == 'Adamax':
            optimizer = keras.optimizers.Adamax()
        elif opt == 'Nadam':
            optimizer = keras.optimizers.Nadam()

                
        model.compile(loss='categorical_crossentropy',
                          optimizer=optimizer,
                          metrics=['accuracy'])
        print('-'*30)
        print('Experiment', i+1)

        csv_logger = CSVLogger('./logs/%s_%d.csv' % (model_name, units), append=False, separator=';')
#             reduce_lr = ReduceLROnPlateau(monitor='val_acc', factor=0.2, patience=5, verbose=0, mode='auto', epsilon=0.0001, cooldown=2, min_lr=0)
#             early_stopping = EarlyStopping(monitor='val_acc', min_delta=0, patience=15, verbose=1, mode='auto')
#             tb = TensorBoard(log_dir='./tb_logs/' + model_name + '_' + str(units), histogram_freq=0, batch_size=32, write_graph=True, write_grads=False, write_images=False, embeddings_freq=0, embeddings_layer_names=None, embeddings_metadata=None)
        history = model.fit(x_train, y_train,
                                batch_size=batch_size,
                                epochs=epochs,
                                verbose=1,
                                validation_data=(x_test, y_test), callbacks=[csv_logger])

        if not os.path.isdir(save_dir):
            os.makedirs(save_dir)
        model_path = os.path.join(save_dir, model_name + ".h5")
#         model.save(model_path)
        score = model.evaluate(x_test, y_test, verbose=0)
        print('Test loss:', score[0])
        print('Test accuracy:', score[1])